In [1]:
import pandas as pd
import copy
from sklearn.linear_model import LinearRegression
import sklearn.metrics as metrics
import numpy as np
from keras import Sequential
from keras.layers import LSTM, Dense, TimeDistributed, Dropout

In [2]:
pokemon_151 = pd.read_csv('Pokemon_151.csv', index_col = 'Unnamed: 0')
pokemon_151

Product                                 Foil  \
0      151: Alakazam ex Collection                  [' Market Price: ']   
1      151: Alakazam ex Collection                  [' Market Price: ']   
2      151: Alakazam ex Collection                  [' Market Price: ']   
3      151: Alakazam ex Collection                  [' Market Price: ']   
4      151: Alakazam ex Collection                  [' Market Price: ']   
...                            ...                                  ...   
11785                        Zubat  ['Reverse Holofoil Market Price: ']   
11786                        Zubat                  [' Market Price: ']   
11787                        Zubat  ['Reverse Holofoil Market Price: ']   
11788                        Zubat                  [' Market Price: ']   
11789                        Zubat  ['Reverse Holofoil Market Price: ']   

           Date Range Market Price  
0          8/5 to 8/7       $27.46  
1         8/8 to 8/10       $26.81  
2        8/11 to 8/13       $26.21  
3        8/14 to 8/16       $25.41  
4        8/17 to 8/19       $23.35  
...               ...          ...  
11785  10/25 to 10/27        $0.20  
11786  10/28 to 10/30        $0.04  
11787  10/28 to 10/30        $0.23  
11788   10/31 to 11/2        $0.03  
11789   10/31 to 11/2        $0.22  

[11790 rows x 4 columns]

In [3]:
len(pokemon_151['Product'].unique())

240

In [4]:
pokemon_151['Foil'].unique()

array(["[' Market Price: ']", "['Reverse Holofoil Market Price: ']",
       "['Holofoil Market Price: ']"], dtype=object)

In [5]:
pokemon_151.replace({'Foil' : { "[' Market Price: ']" : "Normal", "[' Foil Market Price: ']" : "Foil",
                               "['Reverse Holofoil Market Price: ']" : "Reverse Holofoil", 
                               "['Holofoil Market Price: ']" : "Holofoil"}}, inplace=True)

In [6]:
pokemon_151

Product              Foil      Date Range  \
0      151: Alakazam ex Collection            Normal      8/5 to 8/7   
1      151: Alakazam ex Collection            Normal     8/8 to 8/10   
2      151: Alakazam ex Collection            Normal    8/11 to 8/13   
3      151: Alakazam ex Collection            Normal    8/14 to 8/16   
4      151: Alakazam ex Collection            Normal    8/17 to 8/19   
...                            ...               ...             ...   
11785                        Zubat  Reverse Holofoil  10/25 to 10/27   
11786                        Zubat            Normal  10/28 to 10/30   
11787                        Zubat  Reverse Holofoil  10/28 to 10/30   
11788                        Zubat            Normal   10/31 to 11/2   
11789                        Zubat  Reverse Holofoil   10/31 to 11/2   

      Market Price  
0           $27.46  
1           $26.81  
2           $26.21  
3           $25.41  
4           $23.35  
...            ...  
11785        $0.20  
11786        $0.04  
11787        $0.23  
11788        $0.03  
11789        $0.22  

[11790 rows x 4 columns]

In [7]:
sum(pokemon_151['Market Price'] == "$0.00") / len(pokemon_151['Market Price'] == "$0.00")
# 49% of dataset is $0.00

0.49236641221374045

In [8]:
pokemon_151 = pokemon_151[pokemon_151['Market Price'] != '$0.00']
pokemon_151['Market Price'] = pokemon_151['Market Price'].replace({'\$':''}, regex = True)
pokemon_151['Market Price'] = pokemon_151['Market Price'].astype(float)
pokemon_151 = pokemon_151.reset_index(drop=True)
pokemon_151

C:\Users\steve\AppData\Local\Temp\ipykernel_38432\706122419.py:2: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pokemon_151['Market Price'] = pokemon_151['Market Price'].replace({'\$':''}, regex = True)
C:\Users\steve\AppData\Local\Temp\ipykernel_38432\706122419.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pokemon_151['Market Price'] = pokemon_151['Market Price'].astype(float)


Product              Foil      Date Range  \
0     151: Alakazam ex Collection            Normal      8/5 to 8/7   
1     151: Alakazam ex Collection            Normal     8/8 to 8/10   
2     151: Alakazam ex Collection            Normal    8/11 to 8/13   
3     151: Alakazam ex Collection            Normal    8/14 to 8/16   
4     151: Alakazam ex Collection            Normal    8/17 to 8/19   
...                           ...               ...             ...   
5980                        Zubat  Reverse Holofoil  10/25 to 10/27   
5981                        Zubat            Normal  10/28 to 10/30   
5982                        Zubat  Reverse Holofoil  10/28 to 10/30   
5983                        Zubat            Normal   10/31 to 11/2   
5984                        Zubat  Reverse Holofoil   10/31 to 11/2   

      Market Price  
0            27.46  
1            26.81  
2            26.21  
3            25.41  
4            23.35  
...            ...  
5980          0.20  
5981          0.04  
5982          0.23  
5983          0.03  
5984          0.22  

[5985 rows x 4 columns]

In [9]:
def past_prices(num_historical_prices, df):
    dataset = copy.deepcopy(df)
    for n in range(num_historical_prices):
        # whether product matches the product from the previous line
        match_prev_product = [dataset['Product'][i] == dataset['Product'][i+1] for i in range(len(dataset['Product'])-1)]
        # whether foil matches the foil from the previous line
        match_prev_foil = [dataset['Foil'][i] == dataset['Foil'][i+1] for i in range(len(dataset['Foil'])-1)]
        # base case, take the prev market price from the previous row
        if n == 0:
            prev_market_price = dataset['Market Price'][:-1]
        # otherwise take the latest next market price from the next row
        else:
            prev_market_price = dataset[f'Previous Market Price_{n}'][:-1]
            
        dataset = dataset[1:]
        dataset = dataset.reset_index(drop=True)
        dataset[f'Previous Market Price_{n+1}'] = prev_market_price
        prev_match = [match_prev_product[i] and match_prev_foil[i] for i in range(len(match_prev_product))]
        dataset = dataset[prev_match]
        dataset = dataset.reset_index(drop=True)
    return dataset

In [10]:
def future_prices(num_historical_prices, df):
    dataset = copy.deepcopy(df)
    for n in range(num_historical_prices):
        match_next_product = [dataset['Product'][i] == dataset['Product'][i+1] for i in range(len(dataset['Product'])-1)]
        match_next_foil = [dataset['Foil'][i] == dataset['Foil'][i+1] for i in range(len(dataset['Foil'])-1)]
        # base case, take the next market price from the next row
        if n == 0:
            next_market_price = dataset['Market Price'][1:]
        # otherwise take the latest next market price from the next row
        else:
            next_market_price = dataset[f'Next Market Price_{n}'][1:]
                    
        next_market_price = next_market_price.reset_index(drop=True)
        dataset = dataset[:-1]
        dataset = dataset.reset_index(drop=True)
        dataset[f'Next Market Price_{n+1}'] = next_market_price
        next_match = [match_next_product[i] and match_next_foil[i] for i in range(len(match_next_product))]
        dataset = dataset[next_match]
        dataset = dataset.reset_index(drop=True)
    return dataset

In [11]:
# gets the next month of market prices
pokemon_151_future = future_prices(1, pokemon_151)
# obtains the last 15 days worth of prices
pokemon_151_past_future_prices = past_prices(5, pokemon_151_future)
pokemon_151_past_future_prices

Product      Foil      Date Range  Market Price  \
0    151: Alakazam ex Collection    Normal    8/20 to 8/22         22.63   
1    151: Alakazam ex Collection    Normal    8/23 to 8/25         22.63   
2    151: Alakazam ex Collection    Normal    8/26 to 8/28         22.62   
3    151: Alakazam ex Collection    Normal    8/29 to 8/31         22.50   
4    151: Alakazam ex Collection    Normal      9/1 to 9/3         22.42   
..                           ...       ...             ...           ...   
853          Zapdos ex - 202/165  Holofoil  10/16 to 10/18         42.84   
854          Zapdos ex - 202/165  Holofoil  10/19 to 10/21         41.67   
855          Zapdos ex - 202/165  Holofoil  10/22 to 10/24         42.31   
856          Zapdos ex - 202/165  Holofoil  10/25 to 10/27         42.06   
857          Zapdos ex - 202/165  Holofoil  10/28 to 10/30         41.97   

     Next Market Price_1  Previous Market Price_1  Previous Market Price_2  \
0                  22.63                    23.35                    25.41   
1                  22.62                    22.63                    23.35   
2                  22.50                    22.63                    22.63   
3                  22.42                    22.62                    22.63   
4                  22.36                    22.50                    22.62   
..                   ...                      ...                      ...   
853                41.67                    43.75                    46.11   
854                42.31                    42.84                    43.75   
855                42.06                    41.67                    42.84   
856                41.97                    42.31                    41.67   
857                43.11                    42.06                    42.31   

     Previous Market Price_3  Previous Market Price_4  Previous Market Price_5  
0                      26.21                    26.81                    27.46  
1                      25.41                    26.21                    26.81  
2                      23.35                    25.41                    26.21  
3                      22.63                    23.35                    25.41  
4                      22.63                    22.63                    23.35  
..                       ...                      ...                      ...  
853                    43.29                    39.52                    43.81  
854                    46.11                    43.29                    39.52  
855                    43.75                    46.11                    43.29  
856                    42.84                    43.75                    46.11  
857                    41.67                    42.84                    43.75  

[858 rows x 10 columns]

# Data Split

In [12]:
pokemon_151_past_future_prices['Date Range'].unique()

array(['8/20 to 8/22', '8/23 to 8/25', '8/26 to 8/28', '8/29 to 8/31',
       '9/1 to 9/3', '9/4 to 9/6', '9/7 to 9/9', '9/10 to 9/12',
       '9/13 to 9/15', '9/16 to 9/18', '9/19 to 9/21', '9/22 to 9/24',
       '9/25 to 9/27', '9/28 to 9/30', '10/1 to 10/3', '10/4 to 10/6',
       '10/7 to 10/9', '10/10 to 10/12', '10/13 to 10/15',
       '10/16 to 10/18', '10/19 to 10/21', '10/22 to 10/24',
       '10/25 to 10/27', '10/28 to 10/30'], dtype=object)

In [13]:
test = pokemon_151_past_future_prices.loc[pokemon_151_past_future_prices['Date Range'].isin(['10/16 to 10/18', '10/19 to 10/21', '10/22 to 10/24',
       '10/25 to 10/27', '10/28 to 10/30'])]
train = pokemon_151_past_future_prices.loc[pokemon_151_past_future_prices['Date Range'].isin(['8/20 to 8/22', '8/23 to 8/25', '8/26 to 8/28', '8/29 to 8/31',
       '9/1 to 9/3', '9/4 to 9/6', '9/7 to 9/9', '9/10 to 9/12',
       '9/13 to 9/15', '9/16 to 9/18', '9/19 to 9/21', '9/22 to 9/24',
       '9/25 to 9/27', '9/28 to 9/30', '10/1 to 10/3', '10/4 to 10/6',
       '10/7 to 10/9', '10/10 to 10/12', '10/13 to 10/15'])]
test

Product      Foil      Date Range  Market Price  \
19   151: Alakazam ex Collection    Normal  10/16 to 10/18         24.40   
20   151: Alakazam ex Collection    Normal  10/19 to 10/21         25.65   
21   151: Alakazam ex Collection    Normal  10/22 to 10/24         26.64   
22   151: Alakazam ex Collection    Normal  10/25 to 10/27         25.79   
23   151: Alakazam ex Collection    Normal  10/28 to 10/30         25.26   
..                           ...       ...             ...           ...   
853          Zapdos ex - 202/165  Holofoil  10/16 to 10/18         42.84   
854          Zapdos ex - 202/165  Holofoil  10/19 to 10/21         41.67   
855          Zapdos ex - 202/165  Holofoil  10/22 to 10/24         42.31   
856          Zapdos ex - 202/165  Holofoil  10/25 to 10/27         42.06   
857          Zapdos ex - 202/165  Holofoil  10/28 to 10/30         41.97   

     Next Market Price_1  Previous Market Price_1  Previous Market Price_2  \
19                 25.65                    22.82                    25.33   
20                 26.64                    24.40                    22.82   
21                 25.79                    25.65                    24.40   
22                 25.26                    26.64                    25.65   
23                 25.40                    25.79                    26.64   
..                   ...                      ...                      ...   
853                41.67                    43.75                    46.11   
854                42.31                    42.84                    43.75   
855                42.06                    41.67                    42.84   
856                41.97                    42.31                    41.67   
857                43.11                    42.06                    42.31   

     Previous Market Price_3  Previous Market Price_4  Previous Market Price_5  
19                     24.35                    26.56                    31.60  
20                     25.33                    24.35                    26.56  
21                     22.82                    25.33                    24.35  
22                     24.40                    22.82                    25.33  
23                     25.65                    24.40                    22.82  
..                       ...                      ...                      ...  
853                    43.29                    39.52                    43.81  
854                    46.11                    43.29                    39.52  
855                    43.75                    46.11                    43.29  
856                    42.84                    43.75                    46.11  
857                    41.67                    42.84                    43.75  

[374 rows x 10 columns]

In [14]:
X_test = test[[ 'Foil', 'Previous Market Price_1', 'Previous Market Price_2', 'Previous Market Price_3',
              'Previous Market Price_4', 'Previous Market Price_5', 'Market Price']]
y_test = test['Next Market Price_1'].astype(float)
X_train = train[[ 'Foil', 'Previous Market Price_1', 'Previous Market Price_2', 'Previous Market Price_3',
              'Previous Market Price_4', 'Previous Market Price_5', 'Market Price']]
y_train = train['Next Market Price_1'].astype(float)

In [15]:
X_test = pd.get_dummies(X_test, columns = ['Foil'])
X_train = pd.get_dummies(X_train, columns = ['Foil'])

# Linear Regression

In [16]:
classifier = LinearRegression()
classifier.fit(X_train, y_train)

LinearRegression()

In [17]:
coefficients = pd.DataFrame(zip(X_train.columns, classifier.coef_))
coefficients

0         1
0  Previous Market Price_1 -0.656283
1  Previous Market Price_2  0.371770
2  Previous Market Price_3 -0.025742
3  Previous Market Price_4 -0.062820
4  Previous Market Price_5  0.010813
5             Market Price  1.354958
6            Foil_Holofoil  0.270795
7              Foil_Normal -0.270795

In [18]:
y_pred = classifier.predict(X_test)

In [19]:
def regression_results(y_true, y_pred):

    # Regression metrics
    explained_variance=metrics.explained_variance_score(y_true, y_pred)
    mean_absolute_error=metrics.mean_absolute_error(y_true, y_pred) 
    mse=metrics.mean_squared_error(y_true, y_pred) 
#     mean_squared_log_error=metrics.mean_squared_log_error(y_true, y_pred)
    median_absolute_error=metrics.median_absolute_error(y_true, y_pred)
    r2=metrics.r2_score(y_true, y_pred)

    print('explained_variance: ', round(explained_variance,4))    
#     print('mean_squared_log_error: ', round(mean_squared_log_error,4))
    print('r2: ', round(r2,4))
    print('MAE: ', round(mean_absolute_error,4))
    print('MSE: ', round(mse,4))
    print('RMSE: ', round(np.sqrt(mse),4))

In [20]:
regression_results(y_test, y_pred)

explained_variance:  0.9996
r2:  0.9996
MAE:  1.1811
MSE:  3.871
RMSE:  1.9675


# LSTM

In [21]:
X_train = train[['Previous Market Price_5', 'Previous Market Price_4', 'Previous Market Price_3',
              'Previous Market Price_2', 'Previous Market Price_1', 'Market Price']]

X_test = test[['Previous Market Price_5', 'Previous Market Price_4', 'Previous Market Price_3',
              'Previous Market Price_2', 'Previous Market Price_1', 'Market Price']]

In [22]:
model = Sequential()  
model.add(LSTM(1, input_dim=1, return_sequences=False))
# model.add(Dropout(0.5))
# model.add(Dense(8, activation='linear'))
model.add(Dense(1, activation='linear'))  
model.compile(loss='mean_squared_error', optimizer='rmsprop', metrics=['mean_squared_error'])
model.summary()

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 lstm (LSTM)                 (None, 1)                 12        
                                                                 
 dense (Dense)               (None, 1)                 2         
                                                                 
Total params: 14
Trainable params: 14
Non-trainable params: 0
_________________________________________________________________


In [23]:
history = model.fit(X_train, y_train,epochs=30000, validation_data=(X_test, y_test))

Epoch 1/30000
16/16 [==============================] - 3s 37ms/step - loss: 23486.0137 - mean_squared_error: 23486.0137 - val_loss: 10784.3008 - val_mean_squared_error: 10784.3008
Epoch 2/30000
16/16 [==============================] - 0s 4ms/step - loss: 23482.8770 - mean_squared_error: 23482.8770 - val_loss: 10782.7422 - val_mean_squared_error: 10782.7422
Epoch 3/30000
16/16 [==============================] - 0s 5ms/step - loss: 23480.3945 - mean_squared_error: 23480.3945 - val_loss: 10781.2012 - val_mean_squared_error: 10781.2012
Epoch 4/30000
16/16 [==============================] - 0s 5ms/step - loss: 23477.8926 - mean_squared_error: 23477.8926 - val_loss: 10779.6680 - val_mean_squared_error: 10779.6680
Epoch 5/30000
16/16 [==============================] - 0s 5ms/step - loss: 23475.3770 - mean_squared_error: 23475.3770 - val_loss: 10778.1982 - val_mean_squared_error: 10778.1982
Epoch 6/30000
16/16 [==============================] - 0s 5ms/step - loss: 23472.9375 - mean_squared_err

16/16 [==============================] - 0s 5ms/step - loss: 23374.0664 - mean_squared_error: 23374.0664 - val_loss: 10715.6367 - val_mean_squared_error: 10715.6367
Epoch 47/30000
16/16 [==============================] - 0s 5ms/step - loss: 23367.4629 - mean_squared_error: 23367.4629 - val_loss: 10709.0801 - val_mean_squared_error: 10709.0801
Epoch 48/30000
16/16 [==============================] - 0s 5ms/step - loss: 23332.4531 - mean_squared_error: 23332.4531 - val_loss: 10646.6182 - val_mean_squared_error: 10646.6182
Epoch 49/30000
16/16 [==============================] - 0s 5ms/step - loss: 23226.8477 - mean_squared_error: 23226.8477 - val_loss: 10637.7305 - val_mean_squared_error: 10637.7305
Epoch 50/30000
16/16 [==============================] - 0s 5ms/step - loss: 23217.1270 - mean_squared_error: 23217.1270 - val_loss: 10633.4766 - val_mean_squared_error: 10633.4766
Epoch 51/30000
16/16 [==============================] - 0s 5ms/step - loss: 23210.5020 - mean_squared_error: 23210.

16/16 [==============================] - 0s 5ms/step - loss: 23038.9023 - mean_squared_error: 23038.9023 - val_loss: 10529.8193 - val_mean_squared_error: 10529.8193
Epoch 92/30000
16/16 [==============================] - 0s 5ms/step - loss: 23033.0938 - mean_squared_error: 23033.0938 - val_loss: 10525.8086 - val_mean_squared_error: 10525.8086
Epoch 93/30000
16/16 [==============================] - 0s 5ms/step - loss: 23025.7266 - mean_squared_error: 23025.7266 - val_loss: 10518.9463 - val_mean_squared_error: 10518.9463
Epoch 94/30000
16/16 [==============================] - 0s 5ms/step - loss: 23008.7461 - mean_squared_error: 23008.7461 - val_loss: 10507.7988 - val_mean_squared_error: 10507.7988
Epoch 95/30000
16/16 [==============================] - 0s 5ms/step - loss: 22965.4219 - mean_squared_error: 22965.4219 - val_loss: 10488.3643 - val_mean_squared_error: 10488.3643
Epoch 96/30000
16/16 [==============================] - 0s 5ms/step - loss: 22952.3125 - mean_squared_error: 22952.

16/16 [==============================] - 0s 5ms/step - loss: 22778.2129 - mean_squared_error: 22778.2129 - val_loss: 10390.7598 - val_mean_squared_error: 10390.7598
Epoch 137/30000
16/16 [==============================] - 0s 5ms/step - loss: 22773.9707 - mean_squared_error: 22773.9707 - val_loss: 10388.2754 - val_mean_squared_error: 10388.2754
Epoch 138/30000
16/16 [==============================] - 0s 5ms/step - loss: 22769.6152 - mean_squared_error: 22769.6152 - val_loss: 10386.2109 - val_mean_squared_error: 10386.2109
Epoch 139/30000
16/16 [==============================] - 0s 5ms/step - loss: 22765.5645 - mean_squared_error: 22765.5645 - val_loss: 10383.8320 - val_mean_squared_error: 10383.8320
Epoch 140/30000
16/16 [==============================] - 0s 5ms/step - loss: 22761.2051 - mean_squared_error: 22761.2051 - val_loss: 10381.4199 - val_mean_squared_error: 10381.4199
Epoch 141/30000
16/16 [==============================] - 0s 5ms/step - loss: 22756.8164 - mean_squared_error: 2

16/16 [==============================] - 0s 5ms/step - loss: 22585.9199 - mean_squared_error: 22585.9199 - val_loss: 10286.7793 - val_mean_squared_error: 10286.7793
Epoch 182/30000
16/16 [==============================] - 0s 5ms/step - loss: 22581.7207 - mean_squared_error: 22581.7207 - val_loss: 10284.3057 - val_mean_squared_error: 10284.3057
Epoch 183/30000
16/16 [==============================] - 0s 5ms/step - loss: 22577.1992 - mean_squared_error: 22577.1992 - val_loss: 10282.0703 - val_mean_squared_error: 10282.0703
Epoch 184/30000
16/16 [==============================] - 0s 5ms/step - loss: 22572.9746 - mean_squared_error: 22572.9746 - val_loss: 10279.7852 - val_mean_squared_error: 10279.7852
Epoch 185/30000
16/16 [==============================] - 0s 5ms/step - loss: 22568.8008 - mean_squared_error: 22568.8008 - val_loss: 10277.6260 - val_mean_squared_error: 10277.6260
Epoch 186/30000
16/16 [==============================] - 0s 5ms/step - loss: 22564.7207 - mean_squared_error: 2

...

16/16 [==============================] - 0s 6ms/step - loss: 201.8713 - mean_squared_error: 201.8713 - val_loss: 53.4460 - val_mean_squared_error: 53.4460
Epoch 29789/30000
16/16 [==============================] - 0s 6ms/step - loss: 187.9736 - mean_squared_error: 187.9736 - val_loss: 122.4748 - val_mean_squared_error: 122.4748
Epoch 29790/30000
16/16 [==============================] - 0s 6ms/step - loss: 261.8869 - mean_squared_error: 261.8869 - val_loss: 383.3824 - val_mean_squared_error: 383.3824
Epoch 29791/30000
16/16 [==============================] - 0s 6ms/step - loss: 156.1219 - mean_squared_error: 156.1219 - val_loss: 59.6275 - val_mean_squared_error: 59.6275
Epoch 29792/30000
16/16 [==============================] - 0s 6ms/step - loss: 242.4971 - mean_squared_error: 242.4971 - val_loss: 64.6796 - val_mean_squared_error: 64.6796
Epoch 29793/30000
16/16 [==============================] - 0s 6ms/step - loss: 127.8474 - mean_squared_error: 127.8474 - val_loss: 491.1196 - val_mea

16/16 [==============================] - 0s 6ms/step - loss: 244.6908 - mean_squared_error: 244.6908 - val_loss: 1491.9397 - val_mean_squared_error: 1491.9397
Epoch 29836/30000
16/16 [==============================] - 0s 6ms/step - loss: 375.0724 - mean_squared_error: 375.0724 - val_loss: 108.4564 - val_mean_squared_error: 108.4564
Epoch 29837/30000
16/16 [==============================] - 0s 5ms/step - loss: 150.4695 - mean_squared_error: 150.4695 - val_loss: 1247.4183 - val_mean_squared_error: 1247.4183
Epoch 29838/30000
16/16 [==============================] - 0s 5ms/step - loss: 364.7577 - mean_squared_error: 364.7577 - val_loss: 43.2552 - val_mean_squared_error: 43.2552
Epoch 29839/30000
16/16 [==============================] - 0s 6ms/step - loss: 179.9407 - mean_squared_error: 179.9407 - val_loss: 104.5072 - val_mean_squared_error: 104.5072
Epoch 29840/30000
16/16 [==============================] - 0s 5ms/step - loss: 279.3050 - mean_squared_error: 279.3050 - val_loss: 61.2475 - 

16/16 [==============================] - 0s 5ms/step - loss: 192.1719 - mean_squared_error: 192.1719 - val_loss: 72.4861 - val_mean_squared_error: 72.4861
Epoch 29883/30000
16/16 [==============================] - 0s 5ms/step - loss: 184.4464 - mean_squared_error: 184.4464 - val_loss: 102.5646 - val_mean_squared_error: 102.5646
Epoch 29884/30000
16/16 [==============================] - 0s 5ms/step - loss: 163.2459 - mean_squared_error: 163.2459 - val_loss: 37.9720 - val_mean_squared_error: 37.9720
Epoch 29885/30000
16/16 [==============================] - 0s 5ms/step - loss: 214.6342 - mean_squared_error: 214.6342 - val_loss: 279.2938 - val_mean_squared_error: 279.2938
Epoch 29886/30000
16/16 [==============================] - 0s 5ms/step - loss: 222.4592 - mean_squared_error: 222.4592 - val_loss: 42.0941 - val_mean_squared_error: 42.0941
Epoch 29887/30000
16/16 [==============================] - 0s 5ms/step - loss: 137.4355 - mean_squared_error: 137.4355 - val_loss: 416.6858 - val_mea

16/16 [==============================] - 0s 6ms/step - loss: 180.1856 - mean_squared_error: 180.1856 - val_loss: 70.6861 - val_mean_squared_error: 70.6861
Epoch 29930/30000
16/16 [==============================] - 0s 6ms/step - loss: 210.0873 - mean_squared_error: 210.0873 - val_loss: 83.1240 - val_mean_squared_error: 83.1240
Epoch 29931/30000
16/16 [==============================] - 0s 6ms/step - loss: 245.1398 - mean_squared_error: 245.1398 - val_loss: 66.6919 - val_mean_squared_error: 66.6919
Epoch 29932/30000
16/16 [==============================] - 0s 6ms/step - loss: 129.7041 - mean_squared_error: 129.7041 - val_loss: 595.9524 - val_mean_squared_error: 595.9524
Epoch 29933/30000
16/16 [==============================] - 0s 6ms/step - loss: 208.1606 - mean_squared_error: 208.1606 - val_loss: 35.7765 - val_mean_squared_error: 35.7765
Epoch 29934/30000
16/16 [==============================] - 0s 6ms/step - loss: 181.0544 - mean_squared_error: 181.0544 - val_loss: 95.4034 - val_mean_s

16/16 [==============================] - 0s 6ms/step - loss: 168.2516 - mean_squared_error: 168.2516 - val_loss: 36.7714 - val_mean_squared_error: 36.7714
Epoch 29977/30000
16/16 [==============================] - 0s 6ms/step - loss: 237.4590 - mean_squared_error: 237.4590 - val_loss: 488.4538 - val_mean_squared_error: 488.4538
Epoch 29978/30000
16/16 [==============================] - 0s 5ms/step - loss: 214.6779 - mean_squared_error: 214.6779 - val_loss: 102.1143 - val_mean_squared_error: 102.1143
Epoch 29979/30000
16/16 [==============================] - 0s 6ms/step - loss: 181.5648 - mean_squared_error: 181.5648 - val_loss: 96.1788 - val_mean_squared_error: 96.1788
Epoch 29980/30000
16/16 [==============================] - 0s 6ms/step - loss: 194.2061 - mean_squared_error: 194.2061 - val_loss: 522.8064 - val_mean_squared_error: 522.8064
Epoch 29981/30000
16/16 [==============================] - 0s 6ms/step - loss: 188.0310 - mean_squared_error: 188.0310 - val_loss: 55.7733 - val_me

In [26]:
y_pred = np.squeeze(model.predict(X_test))
((y_pred-y_test)**2).mean()

12/12 [==============================] - 0s 1ms/step


50.570318951789496

In [27]:
train_preds = np.squeeze(model.predict(X_train))
((train_preds-y_train)**2).mean()

16/16 [==============================] - 0s 850us/step


106.58780045097441